In [48]:
import pandas as pd
import folium
import xml.etree.ElementTree as ET

### Restaurantes

In [49]:
# Leer xml de restaurantes
tree = ET.parse('datos/restaurantes_v1_es.xml')
root = tree.getroot()

data = []

for service in root.findall("service"):
    restaurante = {}

    restaurante['id'] = service.attrib.get('id')
    restaurante['fechaActualizacion'] = service.attrib.get('fechaActualizacion')

    # Datos básicos
    basic_data = service.find("basicData")
    restaurante["idioma"] = basic_data.find("language").text if basic_data.find("language") is not None else None
    restaurante["nombre"] = basic_data.find("name").text if basic_data.find("name") is not None else None
    restaurante["email"] = basic_data.find("email").text if basic_data.find("email") is not None else None
    restaurante["telefono"] = basic_data.find("phone").text if basic_data.find("phone") is not None else None
    restaurante["web"] = basic_data.find("web").text if basic_data.find("web") is not None else None

    # Datos geográficos
    geo_data = service.find("geoData")
    restaurante["direccion"] = geo_data.find("address").text if geo_data.find("address") is not None else None
    restaurante["codigo_postal"] = geo_data.find("zipcode").text if geo_data.find("zipcode") is not None else None
    restaurante["localidad"] = geo_data.find("locality").text if geo_data.find("locality") is not None else None
    restaurante["pais"] = geo_data.find("country").text if geo_data.find("country") is not None else None
    restaurante["latitud"] = geo_data.find("latitude").text if geo_data.find("latitude") is not None else None
    restaurante["longitud"] = geo_data.find("longitude").text if geo_data.find("longitude") is not None else None

    # Categorías y subcategorías
    categorias = service.findall(".//categoria/item[@name='Categoria']")
    subcategorias = service.findall(".//subcategoria/item[@name='SubCategoria']")
    restaurante["categorias"] = ", ".join([c.text for c in categorias if c is not None])
    restaurante["subcategorias"] = ", ".join([s.text for s in subcategorias if s is not None])

    # Multimedia (solo guardar el primer enlace como ejemplo)
    multimedia = service.findall(".//media[@type='image']")
    restaurante["imagen"] = multimedia[0].find("url").text if multimedia else None

    # Horario
    horario = service.find(".//item[@name='Horario']")
    restaurante["horario"] = horario.text if horario is not None else None

    # Añadir los datos del restaurante a la lista
    data.append(restaurante)

# Crear un DataFrame con los datos extraídos
df_restaurantes = pd.DataFrame(data)

df_restaurantes.head()

id fechaActualizacion idioma                      nombre  \
0  105922         2024-12-11     es                 Roostiq Bar   
1  105886         2024-12-26     es  Experiencity Express Train   
2  105884         2024-12-26     es               Pilar Akaneya   
3  105855         2025-01-07     es                       Tramo   
4  105854         2024-12-26     es                       Varra   

                           email            telefono  \
0                           None  (+34) 91 949 67 10   
1           info@experiencity.es  (+34) 610 42 48 80   
2                           None  (+34) 91 330 76 99   
3         tramo@espaciotramo.com  (+34) 620 09 98 81   
4  contacto@varrarestaurante.com   (+34) 634 234 745   

                                                 web               direccion  \
0  https://www.esmadrid.com/restaurantes/roostiq-bar       del Barquillo, 40   
1  https://www.esmadrid.com/restaurantes/experien...  de Vicente Espinel, 12   
2  https://www.esmadrid.com/restaurantes/pilar-ak...       de Espronceda, 33   
3        https://www.esmadrid.com/restaurantes/tramo  de Eugenio Salazar, 56   
4        https://www.esmadrid.com/restaurantes/varra        de Hermosilla, 7   

  codigo_postal localidad   pais          latitud         longitud  \
0          None      None  Spain  40.423933300000  -3.695462500000   
1         28017      None  Spain  40.435019800000  -3.641122700000   
2         28003      None  Spain  40.440586700000  -3.694902200000   
3         28002      None  Spain  40.448202700000  -3.675405400000   
4         28001      None  Spain  40.426639700000  -3.688344000000   

               categorias                                  subcategorias  \
0  Bares, Tapas, Española                      Gastrobares, Mediterránea   
1           Internacional                                                  
2           Internacional                                       Japonesa   
3                Española                                   De temporada   
4      Tabernas, Española  De temporada, Madrileña, Tradicional renovada   

                                              imagen  \
0  https://estaticos.esmadrid.com/cdn/farfuture/a...   
1  https://estaticos.esmadrid.com/cdn/farfuture/e...   
2  https://estaticos.esmadrid.com/cdn/farfuture/g...   
3  https://estaticos.esmadrid.com/cdn/farfuture/2...   
4  https://estaticos.esmadrid.com/cdn/farfuture/K...   

                                             horario  
0  <p>Lun - Dom: 13:15 - 24:00 h (cocina) / hasta...  
1                           <p>Según la reserva.</p>  
2  <p>Horario de reservas:</p><p>Lun - Vier: 19:3...  
3  <p>Mar - Sáb: 13:30 - 15:30 h / 20:00 - 22:30 ...  
4  <p><strong>Varra Fina (taberna): </strong></p>...

In [50]:
# Filtrar valores no válidos
df_restaurantes = df_restaurantes.dropna(subset=['latitud', 'longitud'])
df_restaurantes['latitud'] = pd.to_numeric(df_restaurantes['latitud'], errors='coerce')
df_restaurantes['longitud'] = pd.to_numeric(df_restaurantes['longitud'], errors='coerce')
df_restaurantes = df_restaurantes.dropna(subset=['latitud', 'longitud'])

In [51]:
from bs4 import BeautifulSoup

# Función para limpiar HTML
def clean_html(html):
    if pd.notnull(html):  # Verificar que no sea NaN
        return BeautifulSoup(html, "html.parser").get_text(strip=True)
    return None  # Manejar valores nulos

# Limpiar la columna de horarios
df_restaurantes['horario'] = df_restaurantes['horario'].apply(clean_html)

# Verificar el resultado
df_restaurantes[['horario']].head()


horario
0  Lun - Dom: 13:15 - 24:00 h (cocina) / hasta la...
1                                  Según la reserva.
2  Horario de reservas:Lun - Vier: 19:30 - 23:30 ...
3       Mar - Sáb: 13:30 - 15:30 h / 20:00 - 22:30 h
4  Varra Fina (taberna):Lun - Jue: 13:30 - 15:00 ...

In [52]:
df_restaurantes = df_restaurantes[['nombre', 'telefono', 'direccion', 'latitud', 'longitud', 'categorias', 'horario']]

In [28]:
df_restaurantes.to_csv('resultados/restaurantes_madrid_limpio.csv', sep=';', index=False)

In [25]:
# Crear popups personalizados para cada restaurante
popups_restaurantes = []

for _, row in df_restaurantes.iterrows():
    popup_content = f"""
    <div style="width: 300px;">
        <h4>{row['nombre']}</h4>
        <p><strong>Horario:</strong> {row['horario']}</p>
        <p><strong>Teléfono:</strong> {row['telefono']}</p>
        <p><strong>Tipo:</strong> {row['categorias']}</p>
        <p><a href="{row['web']}" target="_blank">Ver más información</a></p>
    </div>
    """
    popups_restaurantes.append(folium.Popup(popup_content, max_width=300))


### Parques y jardines

In [53]:
import pandas as pd

df= pd.read_csv('datos/parques-jardines.csv', sep=';', encoding='latin-1')

print(df.columns)

Index(['PK', 'NOMBRE', 'DESCRIPCION-ENTIDAD', 'HORARIO', 'EQUIPAMIENTO',
       'TRANSPORTE', 'DESCRIPCION', 'ACCESIBILIDAD', 'CONTENT-URL',
       'NOMBRE-VIA', 'CLASE-VIAL', 'TIPO-NUM', 'NUM', 'PLANTA', 'PUERTA',
       'ESCALERAS', 'ORIENTACION', 'LOCALIDAD', 'PROVINCIA', 'CODIGO-POSTAL',
       'COD-BARRIO', 'BARRIO', 'COD-DISTRITO', 'DISTRITO', 'COORDENADA-X',
       'COORDENADA-Y', 'LATITUD', 'LONGITUD', 'TELEFONO', 'FAX', 'EMAIL',
       'TIPO'],
      dtype='object')


In [54]:
df_jardines = df[['NOMBRE', 'EQUIPAMIENTO', 'LATITUD','LONGITUD', 'HORARIO']]
df_jardines.columns = ['nombre', 'equipamiento', 'latitud', 'longitud', 'horario']
df_jardines = df_jardines.dropna(subset=['latitud', 'longitud'])
df_jardines

nombre  \
0              Jardines Gregorio Ordóñez   
1       Jardines San Francisco el Grande   
2             Jardines de Andrés Saborit   
3             Jardines de El Buen Retiro   
4             Jardines de Gloria Fuertes   
..                                   ...   
199          Vivero Estufas de El Retiro   
200           Vivero de la Casa de Campo   
201  Vivero municipal de Migas Calientes   
202           Zona verde C/ Fresnedillas   
203         Área Forestal de Tres Cantos   

                                          equipamiento    latitud  longitud  \
0                                     Zonas infantiles  40.433462 -3.678595   
1                                                  NaN  40.410022 -3.714420   
2    Zonas infantiles Zonas adulto mayor Circuito B...  40.446133 -3.698970   
3    Zonas infantiles:  Zona del Pinar (Puerta del ...  40.419641 -3.687934   
4                                        Zona infantil  40.461518 -3.675118   
..                                                 ...        ...       ...   
199                                                NaN  40.409899 -3.682331   
200                                                NaN  40.419842 -3.728697   
201                                                NaN  40.445356 -3.739974   
202  Zona de juegos infantiles Área de juegos para ...  40.477264 -3.743003   
203                                                NaN  40.582363 -3.705431   

                                               horario  
0                                                  NaN  
1                                                  NaN  
2                                                  NaN  
3    Horario del parque    Primavera y verano (de a...  
4                                                  NaN  
..                                                 ...  
199  Invierno de 7 a 23 horas. El acceso al público...  
200  Invierno de 8 a 15 horas Verano de 7 a 14 hora...  
201                                   De 8 a 15 horas.  
202                                                NaN  
203                                                NaN  

[204 rows x 5 columns]

### Centros de salud

In [69]:
df = pd.read_csv('datos/atencion_medica.csv', sep=';', encoding='latin-1')

df.head()

PK                                             NOMBRE  \
0  5855213  Centro Concertado de adicciones (CCAD) Centro ...   
1   134929  Centro Concertado de Atención a las Adicciones...   
2    53123  Centro Concertado de Atención a las Adicciones...   
3    11867  Centro de Atención a las Adicciones (CAD) de A...   
4    11887  Centro de Atención a las Adicciones (CAD) de H...   

                                 DESCRIPCION-ENTIDAD  \
0  El Centro concertado de adicciones Centro form...   
1  El CCAD Cáritas que forma parte de la red del ...   
2  El CCAD  Casa de Campo que forma parte de la r...   
3  Se trata de un centro público que proporciona ...   
4  Se trata de un centro público que proporciona ...   

                                             HORARIO  \
0                 De lunes a viernes de 9 a 17 horas   
1  De lunes a viernes mañanas de 9 a 14 horas, ta...   
2                 De lunes a viernes de 9 a 17 horas   
3  Horario ordinario:   De septiembre a junio:   ...   
4  Horario ordinario:   De septiembre a junio:   ...   

                                        EQUIPAMIENTO  \
0  Valoración interdisciplinar del/de la paciente...   
1  Valoración interdisciplinar del/de la paciente...   
2  Valoración interdisciplinar del paciente. Trat...   
3  Valoración interdisciplinar de cada usuario.  ...   
4  Valoración interdisciplinar de cada usuario.  ...   

                                          TRANSPORTE  \
0                Metro: Alonso Martínez, L4, L5, L10   
1  Bus: 9, 73, N2Metro: Alfonso XIII (L4), Prospe...   
2  Bus: 31, 33, 36, 39, 65, 138 Metro:Puerta del ...   
3  Bus: 6 , 8 , 18 , 19 , 22 , 45 , 47 , 76 , 78 ...   
4  Bus: 73, 87, 104, 112, 120, 125, 153, 172Metro...   

                                         DESCRIPCION  ACCESIBILIDAD  \
0                           Forma de acceso: directo              1   
1                                                NaN              1   
2                           Forma de acceso: directo              1   
3  Forma de acceso: directo, a través de los serv...              1   
4  Acceso: directo, a través de los servicios mun...              1   

                                         CONTENT-URL  \
0  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
2  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
3  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
4  http://www.madrid.es/sites/v/index.jsp?vgnextc...   

                  NOMBRE-VIA  ... COD-DISTRITO    DISTRITO  COORDENADA-X  \
0  HERMANOS ALVAREZ QUINTERO  ...          1.0      CENTRO      440835.0   
1            SANTA HORTENSIA  ...          5.0   CHAMARTIN      443159.0   
2                   PORTUGAL  ...         10.0      LATINA      438577.0   
3                    CHOPERA  ...          2.0  ARGANZUELA      440757.0   
4                     MINAYA  ...         16.0   HORTALEZA      446072.0   

  COORDENADA-Y             LATITUD             LONGITUD     TELEFONO  FAX  \
0    4475437.0   40.42747404776084   -3.697485377509971  914 291 960  NaN   
1    4477482.0  40.446053313442704  -3.6702766124516515  917 440 599  NaN   
2    4474219.0   40.41633059885888  -3.7239914257003304  914 799 499  NaN   
3    4471619.0   40.39305745803064  -3.6980673403694104  915 886 186  NaN   
4    4479929.0  40.468288815918534   -3.636150078507109  913 822 530  NaN   

                              EMAIL  \
0             ctdcentro@cruzroja.es   
1  tto.adicciones@caritasmadrid.org   
2             ctdccampo@cruzroja.es   
3           cadarganzuela@madrid.es   
4           cadhortaleza@madrid. es   

                                                TIPO  
0  /contenido/entidadesYorganismos/CentrosAtencio...  
1  /contenido/entidadesYorganismos/CentrosAtencio...  
2  /contenido/entidadesYorganismos/CentrosAtencio...  
3  /contenido/entidadesYorganismos/CentrosAtencio...  
4  /contenido/entidadesYorganismos/CentrosAtencio...  

[5 rows x 32 column

In [38]:
df.columns

Index(['PK', 'NOMBRE', 'DESCRIPCION-ENTIDAD', 'HORARIO', 'EQUIPAMIENTO',
       'TRANSPORTE', 'DESCRIPCION', 'ACCESIBILIDAD', 'CONTENT-URL',
       'NOMBRE-VIA', 'CLASE-VIAL', 'TIPO-NUM', 'NUM', 'PLANTA', 'PUERTA',
       'ESCALERAS', 'ORIENTACION', 'LOCALIDAD', 'PROVINCIA', 'CODIGO-POSTAL',
       'COD-BARRIO', 'BARRIO', 'COD-DISTRITO', 'DISTRITO', 'COORDENADA-X',
       'COORDENADA-Y', 'LATITUD', 'LONGITUD', 'TELEFONO', 'FAX', 'EMAIL',
       'TIPO'],
      dtype='object')

In [70]:
df_salud = df[['NOMBRE', 'DESCRIPCION-ENTIDAD', 'LATITUD','LONGITUD', 'HORARIO', 'TELEFONO']]
df_salud.columns = ['nombre', 'descripcion', 'latitud', 'longitud', 'horario', 'telefono']

df_salud['latitud'] = pd.to_numeric(df_salud['latitud'], errors='coerce')
df_salud['longitud'] = pd.to_numeric(df_salud['longitud'], errors='coerce')

df_salud = df_salud.dropna(subset=['latitud', 'longitud'])
df_salud

C:\Users\Multivac Desktop\AppData\Local\Temp\ipykernel_15768\2193207688.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_salud['latitud'] = pd.to_numeric(df_salud['latitud'], errors='coerce')
C:\Users\Multivac Desktop\AppData\Local\Temp\ipykernel_15768\2193207688.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_salud['longitud'] = pd.to_numeric(df_salud['longitud'], errors='coerce')


nombre  \
0    Centro Concertado de adicciones (CCAD) Centro ...   
1    Centro Concertado de Atención a las Adicciones...   
2    Centro Concertado de Atención a las Adicciones...   
3    Centro de Atención a las Adicciones (CAD) de A...   
4    Centro de Atención a las Adicciones (CAD) de H...   
..                                                 ...   
268                                 Sanatorio Esquerdo   
269    Servicio de Inmunoprofilaxis de la Rabia Humana   
270  Unidad de Salud Mental de niños y adolescentes...   
271  Unidad de Salud Mental de niños y adolescentes...   
272                               Unidad móvil Madroño   

                                           descripcion    latitud  longitud  \
0    El Centro concertado de adicciones Centro form...  40.427474 -3.697485   
1    El CCAD Cáritas que forma parte de la red del ...  40.446053 -3.670277   
2    El CCAD  Casa de Campo que forma parte de la r...  40.416331 -3.723991   
3    Se trata de un centro público que proporciona ...  40.393057 -3.698067   
4    Se trata de un centro público que proporciona ...  40.468289 -3.636150   
..                                                 ...        ...       ...   
268                                                NaN  40.381917 -3.757900   
269                                                NaN  40.428977 -3.672161   
270                                                NaN  40.472758 -3.718007   
271                                                NaN  40.465445 -3.693604   
272                                                NaN  40.420548 -3.717966   

                                               horario  \
0                   De lunes a viernes de 9 a 17 horas   
1    De lunes a viernes mañanas de 9 a 14 horas, ta...   
2                   De lunes a viernes de 9 a 17 horas   
3    Horario ordinario:   De septiembre a junio:   ...   
4    Horario ordinario:   De septiembre a junio:   ...   
..                                                 ...   
268                                                NaN   
269           De lunes a viernes de 8:30 a 14:00 horas   
270                         Consultar telefónicamente.   
271                         Consultal telefónicamente.   
272  De lunes a viernes de 12 a 14 horas Fines de s...   

                                              telefono  
0                                          914 291 960  
1                                          917 440 599  
2                                          914 799 499  
3                                          915 886 186  
4                                          913 822 530  
..                                                 ...  
268                                        917 061 100  
269  914 801 360 ( En este teléfono solo se atender...  
270                          913 733 597 / 913 733 977  
271                                        915 886 675  
272                                                NaN  

[272 rows x 6 columns]

### Fuentes potables

In [57]:
df = pd.read_csv('datos/fuentes_potables.csv', sep=';')
df = df.dropna(subset=['LATITUD', 'LONGITUD', 'USO'])
df = df[ df['ESTADO'] == 'OPERATIVO']
df

ID DESC_CLASIFICACION  COD_BARRIO         BARRIO  COD_DISTRITO  \
3     3530535   Fuentes de beber         159    COSTILLARES            15   
5     3530650   Fuentes de beber          83     PEÑAGRANDE             8   
6     3530868   Fuentes de beber          16            SOL             1   
7     3531364   Fuentes de beber          84          PILAR             8   
11    3567461   Fuentes de beber          14       JUSTICIA             1   
...       ...                ...         ...            ...           ...   
2217  9697995   Fuentes de beber          91  CASA DE CAMPO             9   
2218  9697996   Fuentes de beber          92      ARGÜELLES             9   
2221  9697994   Fuentes de beber          92      ARGÜELLES             9   
2222  9697997   Fuentes de beber          92      ARGÜELLES             9   
2223  9869788   Fuentes de beber         215     CORRALEJOS            21   

                 DISTRITO     ESTADO  COORD_GIS_X  COORD_GIS_Y SISTEMA_COORD  \
3           CIUDAD LINEAL  OPERATIVO   443892.050  4481542.010        ETRS89   
5     FUENCARRAL-EL PARDO  OPERATIVO   438406.713  4480606.820        ETRS89   
6                  CENTRO  OPERATIVO   439879.020  4474144.040        ETRS89   
7     FUENCARRAL-EL PARDO  OPERATIVO   440030.600  4480481.601        ETRS89   
11                 CENTRO  OPERATIVO   440629.770  4475283.340        ETRS89   
...                   ...        ...          ...          ...           ...   
2217    MONCLOA - ARAVACA  OPERATIVO   439293.082  4474998.237        ETRS89   
2218    MONCLOA - ARAVACA  OPERATIVO   439529.317  4474917.653        ETRS89   
2221    MONCLOA - ARAVACA  OPERATIVO   439365.950  4474955.694        ETRS89   
2222    MONCLOA - ARAVACA  OPERATIVO   439512.799  4474970.048        ETRS89   
2223              BARAJAS  OPERATIVO   448455.578  4479663.962        ETRS89   

      ...  NUM_VIA  COD_POSTAL  \
3     ...       49     28033.0   
5     ...       36     28035.0   
6     ...        6     28012.0   
7     ...       45     28029.0   
11    ...        8     28004.0   
...   ...      ...         ...   
2217  ...      NaN     28008.0   
2218  ...      NaN     28008.0   
2221  ...      NaN     28008.0   
2222  ...      NaN     28008.0   
2223  ...        5     28042.0   

                                          DIRECCION_AUX         NDP  \
3                                   JUNTO ÁREA INFANTIL  20184185.0   
5                              EN EL PARQUE DE ENFRENTE  11044479.0   
6                                cv Travesía de Bringas  11007722.0   
7                                    CALLE RIBADAVIA 27  31041111.0   
11    JARDINES DEL ARQUITECTO RIBERA JUNTO A PARQUE ...  11005217.0   
...                                                 ...         ...   
2217                                                NaN         NaN   
2218                                                NaN         NaN   
2221                                                NaN         NaN   
2222                                                NaN         NaN   
2223                  Parque Juan Carlos I.  Pirámide 2         NaN   

          FECHA_INSTALACION   CODIGO_INTERNO CONTRATO_COD  UBICACION  \
3     2017-06-13 00:00:00.0      FUE_15_0120        FUE22         ZV   
5                       NaN      FUE_08_0150        FUE22         ZV   
6     2017-06-22 00:00:00.0      FUE_01_0044        FUE22         VP   
7     2017-07-21 00:00:00.0      FUE_08_0062        FUE22         ZV   
11    2017-10-09 00:00:00.0      FUE_01_0045        FUE22         ZV   
...                     ...              ...          ...        ...   
2217                    NaN  FUEP_09_26_0001         PV24         ZV   
2218                    NaN  FUEP_09_26_0005         PV24         ZV   
2221                    NaN  FUEP_09_26_0002         PV24         ZV   
2222                    NaN  FUEP_09_26_0004         PV24         ZV   
2223  2025-01-09 00:00:00.0  FUEP_21_12_0040         PV24         ZV   

In [43]:
df.columns

Index(['ID', 'DESC_CLASIFICACION', 'COD_BARRIO', 'BARRIO', 'COD_DISTRITO',
       'DISTRITO', 'ESTADO', 'COORD_GIS_X', 'COORD_GIS_Y', 'SISTEMA_COORD',
       'LATITUD', 'LONGITUD', 'TIPO_VIA', 'NOM_VIA', 'NUM_VIA', 'COD_POSTAL',
       'DIRECCION_AUX', 'NDP', 'FECHA_INSTALACION', 'CODIGO_INTERNO',
       'CONTRATO_COD', 'UBICACION', 'USO', 'MODELO'],
      dtype='object')

In [58]:
df_personas = df[ (df['USO'] == 'PERSONAS') | (df['USO'] == 'PERSONAS_Y_MASCOTAS') ]
df_personas = df_personas[['CODIGO_INTERNO', 'LATITUD','LONGITUD']]
df_personas.columns = ['codigo', 'latitud', 'longitud']



df_mascotas = df[ df['USO'] == 'MASCOTAS' ]
df_mascotas = df_mascotas[['CODIGO_INTERNO','LATITUD','LONGITUD']]
df_mascotas.columns = ['codigo', 'latitud', 'longitud']

### Mapa

In [65]:
import folium
from folium.plugins import MarkerCluster





def generar_mapa(mapa, data, tipo):
    

    # Diccionario de iconos según el tipo
    iconos = {
        "Restaurantes": "cutlery",
        "Parques": "tree",
        "Fuentes": "tint",
        "Fuentes mascotas": "dog",
        "Centros de Salud": "medkit"
    }

    cluster = MarkerCluster(name=tipo).add_to(mapa)  # Añadimos una capa para cada tipo

    # Recorremos el dataframe para añadir marcadores personalizados
    for _, row in data.iterrows():
        # Elegir icono y texto del popup según el tipo
        icono = iconos.get(tipo, "info-sign")
        texto_popup = ""

        if tipo == "Restaurantes":
            texto_popup = f"<b>{row['nombre']}</b><br>Cocina: {row['categorias']}<br>Horario: {row['horario']}<br>Teléfono: {row['telefono']}"
        elif tipo == "Parques":
            texto_popup = f"<b>{row['nombre']}</b><br>Equipamiento: {row['equipamiento']}<br>Horario: {row['horario']}"
        elif tipo == "Fuentes":
            texto_popup = f"<b>{row['codigo']}</b><br>Fuente potable disponible."
        elif tipo == "Fuentes mascotas":
            texto_popup = f"<b>{row['codigo']}</b><br>Fuente para mascotas."
        elif tipo == "Centros de Salud":
            texto_popup = f"<b>{row['nombre']}</b><br>Descripción: {row['descripcion']}<br>Horario: {row['horario']}<br>Teléfono: {row['telefono']}"

        # Añadir el marcador al mapa
        folium.Marker(
            location=[row["latitud"], row["longitud"]],
            popup=folium.Popup(texto_popup, max_width=300),
            icon=folium.Icon(icon=icono, prefix="fa", color="blue")
        ).add_to(cluster)





In [71]:

# Generamos el mapa de madrid
mapa = folium.Map([40.428, -3.76], zoom_start=12)

# Dataset de restaurantes
generar_mapa(mapa, df_restaurantes, 'Restaurantes')

# Dataset de jardines
generar_mapa(mapa, df_jardines, 'Parques')

# Dataset de fuentes
generar_mapa(mapa, df_personas, 'Fuentes')

# Dataset de fuentes mascotas
generar_mapa(mapa, df_mascotas, 'Fuentes mascotas')

# Dataset de salud
generar_mapa(mapa, df_salud, 'Centros de Salud')

# Añadir control de capas para alternar entre ellas
folium.LayerControl().add_to(mapa)

display(mapa)

In [72]:
mapa.save('resultados/mapa_servicios.html')

In [27]:
import folium.plugins

# Crear el mapa centrado en Madrid
m = folium.Map([40.428, -3.76], zoom_start=12)

# Añadir los alojamientos como una capa GeoJson
alojamientos_layer = folium.FeatureGroup(name='Alojamientos', show=True)

# Añadir markers de alojamientos
locations = list(zip(df_alojamientos.latitud, df_alojamientos.longitud))
cluster = folium.plugins.MarkerCluster(locations=locations,                     
               popups=df_alojamientos["nombre"].tolist())

alojamientos_layer.add_child(cluster)


# Agregar la capa al mapa
alojamientos_layer.add_to(m)


# Añadir los restaurantes como una capa GeoJson
restaurantes_layer = folium.FeatureGroup(name='Restaurantes', show=True)

# Añadir markers de restaurantes
locations = list(zip(df_restaurantes.latitud, df_restaurantes.longitud))
cluster_restaur = folium.plugins.MarkerCluster(locations=locations,                     
               popups=popups_restaurantes)

restaurantes_layer.add_child(cluster_restaur)


# Agregar la capa al mapa
restaurantes_layer.add_to(m)



# Añadir el control de capas para activar/desactivar las capas
folium.LayerControl().add_to(m)

# Guardar y mostrar el mapa
m.save('resultados/mapa_restauracion.html')
m